# Descargar automáticamente del SMN
A partir de la ejecución del siguiente código: 
1. Se descargan los archivos de datos horarios del Servicio Meteorológico Nacional de las fechas seleccionadas.
2. Se estandarizan los mismos y compila en una única tabla.
3. Se los exporta como archivo CSV.

Fuente: https://www.smn.gob.ar/descarga-de-datos

### DH. Datos Horarios
Dato meteorológico de todas las estaciones de superficie del país
Datos de temperatura, presión, viento y humedad de las estaciones meteorológicas de todo el país.

In [1]:
#Cargar librerías
import requests
import pandas as pd
from datetime import datetime, date, timedelta
from os import mkdir, rmdir, remove, path

In [2]:
# Definir fechas
sdate = date(2018, 2, 1)   # fecha de inicio (año, mes, día)
edate = date(2018, 2, 28)   # fecha de fin (año, mes, día)

delta = edate - sdate

In [3]:
# Descarga de datos
dir = "meteodata" #carpeta de destino de los archivos
mkdir(str(dir)) 

for i in range(delta.days + 1):
    date = str(sdate + timedelta(days=i)).replace('-', '')
    url = 'https://ssl.smn.gob.ar/dpd/descarga_opendata.php?file=observaciones/datohorario' + date + '.txt'
    r = requests.get(url, allow_redirects=True)
    if 'El archivo no existe.' in str(r.content):
        print(date + " does not exist")
    else:
        with open('./' + dir + '/' + date + '.txt', 'wb') as f: f.write(r.content) 

20180211 does not exist


In [4]:
#Filtrado y combinación de archivos
estacion = 'ROSARIO AERO' #filtro de selección de estación

out = pd.DataFrame(columns = ['Fecha', 'Hora', 'Temp[ºC]', 'Hum[%]', 'Pres[hPa]', 'VDir[gr]', 'VVel[km/h]', 'Estacion'])

for i in range(delta.days + 1):
    date = str(sdate + timedelta(days=i)).replace('-', '')
    if path.isfile('./' + dir + '/'  + date + '.txt'):
        df = pd.read_fwf('./' + dir + '/'  + date + '.txt', header = None, index_col = False, 
                names = ['Fecha', 'Hora', 'Temp[ºC]', 'Hum[%]', 'Pres[hPa]', 'VDir[gr]', 'VVel[km/h]', 'Estacion'])
        df1 = df[df['Estacion'] == estacion] 
        out = out.append(df1, ignore_index=True)
    else:
        print(date + " does not exist")

    
display(out.head())
display(out.tail())

20180211 does not exist


Fecha Hora Temp[ºC] Hum[%] Pres[hPa] VDir[gr] VVel[km/h]      Estacion
0  01022018    0     22.2     75    1013.9      180          9  ROSARIO AERO
1  01022018    1     22.1     76    1013.9      180          6  ROSARIO AERO
2  01022018    2     20.6     82    1013.3      180         13  ROSARIO AERO
3  01022018    3     20.5     81    1012.9      160          9  ROSARIO AERO
4  01022018    4     19.4     85    1012.7      180          6  ROSARIO AERO

Fecha Hora Temp[ºC] Hum[%] Pres[hPa] VDir[gr] VVel[km/h]      Estacion
643  28022018   19     28.8     44    1010.0       90          9  ROSARIO AERO
644  28022018   20     27.4     56    1010.8       70         11  ROSARIO AERO
645  28022018   21     26.4     65    1011.6       70          9  ROSARIO AERO
646  28022018   22     25.8     66    1011.8       50          9  ROSARIO AERO
647  28022018   23     25.9     68    1012.3      110         11  ROSARIO AERO

In [5]:
#Estandarización
df = out

df['Horario'] = df['Fecha'].map(str) + ' ' + df['Hora'].map(str) + ':00'
df['Horario'] = pd.to_datetime(df['Horario'], format ='%d%m%Y %H:%M') 

df['Temp[ºC]'] = df['Temp[ºC]'].astype(float)
df['Hum[%]'] = df['Hum[%]'].astype(float)
df['Pres[hPa]'] = df['Pres[hPa]'].astype(float)
df['VDir[gr]'] = df['VDir[gr]'].astype(float)
df['VVel[km/h]'] = df['VVel[km/h]'].astype(float)

df = df[['Horario', 'Temp[ºC]', 'Hum[%]', 'Pres[hPa]', 'VDir[gr]', 'VVel[km/h]']]

print(df.info())

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 648 entries, 0 to 647
Data columns (total 6 columns):
 #   Column      Non-Null Count  Dtype         
---  ------      --------------  -----         
 0   Horario     648 non-null    datetime64[ns]
 1   Temp[ºC]    648 non-null    float64       
 2   Hum[%]      648 non-null    float64       
 3   Pres[hPa]   648 non-null    float64       
 4   VDir[gr]    648 non-null    float64       
 5   VVel[km/h]  648 non-null    float64       
dtypes: datetime64[ns](1), float64(5)
memory usage: 30.5 KB
None


In [6]:
#Borra archivos anteriores y exporta la tabla
file = 'datosRosario.csv' #nombre del archivo de destino

df.to_csv(file, index = False) 

for i in range(delta.days + 1):
    date = str(sdate + timedelta(days=i)).replace('-', '')
    if path.isfile('./' + dir + '/'  + date + '.txt'):
        remove('./' + dir + '/' + date + '.txt')
    else:
        print(date + " does not exist")
rmdir(str(dir))

20180211 does not exist
